In [5]:
import gradio as gr
import requests
from Bio.PDB import PDBParser
from gradio_molecule3d import Molecule3D
import numpy as np

# Function to fetch a PDB file from RCSB PDB
def fetch_pdb(pdb_id):
    pdb_url = f'https://files.rcsb.org/download/{pdb_id}.pdb'
    pdb_path = f'{pdb_id}.pdb'
    response = requests.get(pdb_url)
    if response.status_code == 200:
        with open(pdb_path, 'wb') as f:
            f.write(response.content)
        return pdb_path
    else:
        return None

# Function to process the PDB file and return random predictions
def process_pdb(pdb_id, segment):
    pdb_path = fetch_pdb(pdb_id)
    if not pdb_path:
        return "Failed to fetch PDB file", None, None

    parser = PDBParser(QUIET=True)
    structure = parser.get_structure('protein', pdb_path)
    
    try:
        chain = structure[0][segment]
    except KeyError:
        return "Invalid Chain ID", None, None

    sequence = [residue.get_resname() for residue in chain if residue.id[0] == ' ']
    random_scores = np.random.rand(len(sequence))

    result_str = "\n".join(
        f"{seq} {res.id[1]} {score:.2f}" 
        for seq, res, score in zip(sequence, chain, random_scores)
    )

    # Save the predictions to a file
    prediction_file = f"{pdb_id}_predictions.txt"
    with open(prediction_file, "w") as f:
        f.write(result_str)
    
    return result_str, pdb_path, prediction_file

#reps = [{"model": 0, "style": "cartoon", "color": "spectrum"}]

reps =    [
        {
          "model": 0,
          "style": "cartoon",
          "color": "whiteCarbon",
          "residue_range": "",
          "around": 0,
          "byres": False,
        },
        {
          "model": 0,
          "chain": "A",
          "resname": "HIS",
          "style": "stick",
          "color": "red"
        }
      ]


# Gradio UI
with gr.Blocks() as demo:
    gr.Markdown("# Protein Binding Site Prediction (Random Scores)")

    with gr.Row():
        pdb_input = gr.Textbox(value="2IWI", label="PDB ID", placeholder="Enter PDB ID here...")
        segment_input = gr.Textbox(value="A", label="Chain ID", placeholder="Enter Chain ID here...")
        visualize_btn = gr.Button("Visualize Structure")
        prediction_btn = gr.Button("Predict Random Binding Site Scores")

    molecule_output = Molecule3D(label="Protein Structure", reps=reps)
    predictions_output = gr.Textbox(label="Binding Site Predictions")
    download_output = gr.File(label="Download Predictions")

    visualize_btn.click(fetch_pdb, inputs=[pdb_input], outputs=molecule_output)
    prediction_btn.click(process_pdb, inputs=[pdb_input, segment_input], outputs=[predictions_output, molecule_output, download_output])

    gr.Markdown("## Examples")
    gr.Examples(
        examples=[
            ["2IWI", "A"],
            ["7RPZ", "B"],
            ["3TJN", "C"]
        ],
        inputs=[pdb_input, segment_input],
        outputs=[predictions_output, molecule_output, download_output]
    )

demo.launch()

* Running on local URL:  http://127.0.0.1:7864

To create a public link, set `share=True` in `launch()`.


In [4]:
import gradio as gr
from gradio_molecule3d import Molecule3D


example = Molecule3D().example_value()


reps =    [
        {
          "model": 0,
          "style": "cartoon",
          "color": "whiteCarbon",
          "residue_range": "",
          "around": 0,
          "byres": False,
        },
        {
          "model": 0,
          "chain": "A",
          "resname": "HIS",
          "style": "stick",
          "color": "red"
        }
      ]



def predict(x):
    print("predict function", x)
    print(x.name)
    return x

with gr.Blocks() as demo:
    gr.Markdown("# Molecule3D")
    inp = Molecule3D(label="Molecule3D", reps=reps)
    out = Molecule3D(label="Output", reps=reps)

    btn = gr.Button("Predict")
    gr.Markdown(""" 
    You can configure the default rendering of the molecule by adding a list of representations
    <pre>
        reps =    [
        {
          "model": 0,
          "style": "cartoon",
          "color": "whiteCarbon",
          "residue_range": "",
          "around": 0,
          "byres": False,
        },
        {
          "model": 0,
          "chain": "A",
          "resname": "HIS",
          "style": "stick",
          "color": "red"
        }
      ]
    </pre>
    """)
    btn.click(predict, inputs=inp, outputs=out)


if __name__ == "__main__":
    demo.launch()

* Running on local URL:  http://127.0.0.1:7863

To create a public link, set `share=True` in `launch()`.


In [8]:
import gradio as gr
import requests
from Bio.PDB import PDBParser
from gradio_molecule3d import Molecule3D
import numpy as np
from matplotlib import cm

# Function to fetch a PDB file from RCSB PDB
def fetch_pdb(pdb_id):
    pdb_url = f'https://files.rcsb.org/download/{pdb_id}.pdb'
    pdb_path = f'{pdb_id}.pdb'
    response = requests.get(pdb_url)
    if response.status_code == 200:
        with open(pdb_path, 'wb') as f:
            f.write(response.content)
        return pdb_path
    else:
        return None

# Function to process the PDB file and return random predictions
def process_pdb(pdb_id, segment):
    pdb_path = fetch_pdb(pdb_id)
    if not pdb_path:
        return "Failed to fetch PDB file", None, None, None

    parser = PDBParser(QUIET=True)
    structure = parser.get_structure('protein', pdb_path)

    try:
        chain = structure[0][segment]
    except KeyError:
        return "Invalid Chain ID", None, None, None

    sequence = [residue.get_resname() for residue in chain if residue.id[0] == ' ']
    random_scores = np.random.rand(len(sequence))

    # Normalize scores for coloring (0 = blue, 1 = red)
    normalized_scores = (random_scores - np.min(random_scores)) / (np.max(random_scores) - np.min(random_scores))
    colors = [cm.get_cmap('coolwarm')(score)[:3] for score in normalized_scores]
    hex_colors = [f'#{int(r*255):02x}{int(g*255):02x}{int(b*255):02x}' for r, g, b in colors]

    # Result string and representation
    result_str = "\n".join(
        f"{seq} {res.id[1]} {score:.2f}" 
        for seq, res, score in zip(sequence, chain, random_scores)
    )

    # Representation for the protein structure
    reps = [
        {
            "model": 0,
            "style": "cartoon",
            "color": "whiteCarbon"
        }
    ] + [
        {
            "model": 0,
            "style": "cartoon",
            "residue_index": i,
            "color": color
        }
        for i, color in enumerate(hex_colors)
    ]

    # Save the predictions to a file
    prediction_file = f"{pdb_id}_predictions.txt"
    with open(prediction_file, "w") as f:
        f.write(result_str)
    
    return result_str, reps, prediction_file

# Gradio UI
with gr.Blocks() as demo:
    gr.Markdown("# Protein Binding Site Prediction (Random Scores)")

    with gr.Row():
        pdb_input = gr.Textbox(value="2IWI", label="PDB ID", placeholder="Enter PDB ID here...")
        segment_input = gr.Textbox(value="A", label="Chain ID", placeholder="Enter Chain ID here...")
        visualize_btn = gr.Button("Visualize Structure")
        prediction_btn = gr.Button("Predict Random Binding Site Scores")

    molecule_output = Molecule3D(label="Protein Structure", reps=reps)
    predictions_output = gr.Textbox(label="Binding Site Predictions")
    download_output = gr.File(label="Download Predictions")

    prediction_btn.click(
        fn=process_pdb,
        inputs=[pdb_input, segment_input],
        outputs=[predictions_output, molecule_output, download_output]
    )

    gr.Markdown("## Examples")
    gr.Examples(
        examples=[
            ["2IWI", "A"],
            ["7RPZ", "B"],
            ["3TJN", "C"]
        ],
        inputs=[pdb_input, segment_input],
        outputs=[predictions_output, molecule_output, download_output]
    )

demo.launch()

* Running on local URL:  http://127.0.0.1:7867

To create a public link, set `share=True` in `launch()`.


/var/folders/tm/ym2tckv54b96ws82y3b7cqhh0000gn/T/ipykernel_11794/4072855226.py:39: MatplotlibDeprecationWarning: The get_cmap function was deprecated in Matplotlib 3.7 and will be removed in 3.11. Use ``matplotlib.colormaps[name]`` or ``matplotlib.colormaps.get_cmap()`` or ``pyplot.get_cmap()`` instead.
  colors = [cm.get_cmap('coolwarm')(score)[:3] for score in normalized_scores]
Traceback (most recent call last):
  File "/Users/thorben_froehlking/anaconda3/envs/LLM/lib/python3.12/site-packages/gradio/queueing.py", line 622, in process_events
    response = await route_utils.call_process_api(
               ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "/Users/thorben_froehlking/anaconda3/envs/LLM/lib/python3.12/site-packages/gradio/route_utils.py", line 323, in call_process_api
    output = await app.get_blocks().process_api(
             ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "/Users/thorben_froehlking/anaconda3/envs/LLM/lib/python3.12/site-packages/gradio/blocks.py", line 2024, in